In [1]:
import random
from tqdm.notebook import tqdm
import multiprocessing
import pandas as pd

In [130]:
def generate_balanced_brackets(n, min_depth, max_depth):
    sequence = ''
    stack = []
    
    # for i in range(min_depth):
    #     sequence += '('
    #     stack.append('(')
    start = random.randint(0, n - 2*min_depth)
    # print(start)
    
    for i in range(n):
        if i > start and i < start + min_depth and max_depth > len(stack):
            sequence += '('
            stack.append('(')
            continue
        open_or_close = random.choice([0, 1]) and stack
        left = n - i
        # print(left, n, i, min_depth)
        if left < len(stack) or (not open_or_close and len(stack) == left) or len(stack) == max_depth:
            open_or_close = 1
        if open_or_close:
            sequence += ')'
            stack.pop()
        else:
            sequence += '('
            stack.append('(')
    
    return sequence

def is_balanced(s):
    stack = []
    max_depth = 0
    count = 0
    
    for bracket in s:
        if bracket == ')':
            if stack:
                stack.pop()
            else:
                stack.append(bracket)
                break
        else:
            stack.append(bracket)
            max_depth = max(max_depth, len(stack))
    
    for bracket in s:
        if bracket == '(':
            count += 1
        else:
            count -= 1
                
    if stack:
        return -1 * max_depth, count
    return max_depth, count

def generate_bracket_sequence(n, depth):
    brackets = ['(', ')']
    start = random.randint(0, n - depth)
    max_depth = 0
    stack = []
    
    sequence = '('
    for i in range(n-1):
        if i > start and i < start + depth:
            sequence += '('
            stack.append('(')
            continue
        if len(stack) < depth:
            sequence += random.choice(brackets)
            stack.append(sequence[-1])
        else:
            sequence += ')'
            stack.pop()
        if sequence[-1] == '(':
            stack.append('(')
        max_depth = max(max_depth, len(stack))
    if is_balanced(sequence)[1] == 0:
        return sequence
    else:
        return sequence + random.choice(brackets)
    # seq = generate_balanced_brackets(n, depth, depth)
    # bal = is_balanced(seq)
    # while bal[0] != -1*depth:
    #     seq2 = seq
    #     index = random.randint(0, n-1)
    #     if seq[index] == '(':
    #         seq2 = seq[:index] + ')' + seq[index+1:]
    #     else:
    #         seq2 = seq[:index] + '(' + seq[index+1:]
    #     bal = is_balanced(seq2)
    # return seq2
    
def generate_bracket_sequence_2(n, min_count):
    brackets = ['(', ')']
    
    sequence = ''
    for _ in range(n):
        sequence += random.choice(brackets)
    bal = is_balanced(sequence)
    if bal[0] < 0:
        if abs(bal[1]) >= min_count:
            return generate_bracket_sequence_2(n, min_count)
        return sequence
    else:
        return generate_bracket_sequence_2(n, min_count)

In [167]:
# for _ in range(100):
# s = generate_bracket_sequence(512, 256)
s = generate_bracket_sequence_2(512, 5)
    # if is_balanced(s)[0] != -5:
print(is_balanced(s), s)

(-5, -4) (()(((())))())())(())))())))((()(()(()(())))))()))))()()(()((())()((((((()(()()()))()(()((()(())()())()((((((())())()())))())()()(()))(()(((())())())())(()()(()()())()()(()((((()((((((()(((()))(()))))()((()()))))))(()()()(()))())))())))())((()()))(()((()()))())))(())()))))()(((()(()(())()(())(()((()()())())((()()))()()())(()()))))()((()))(())()()()(((()()(((((((((()))))((())(())()))))))((((())()()())()()()((()))((())()()(())()(((())())(((((())((()))()((()()()()())())()))))()(()()(()())()())(()())())((()))))


In [132]:
s = generate_balanced_brackets(100, 1, 1)
print(is_balanced(s), s)

(1, 0) ()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()()


In [112]:

balanced_df = pd.DataFrame(columns=['sequence', 'stack_depth', 'count'])

seqs = [0 for i in range(400)]

generated_seqs = set()

gen = [i for i in range(2, 10)] + [i for i in range(10, 101, 10)]
print(f'Generating sequences in the following stack depths: {gen}')

for j in tqdm(gen):
    while True:
        length = 512
        
        sequence = generate_balanced_brackets(length, j, j)
        balanced, count = is_balanced(sequence)
        
        if seqs[balanced] == 1000 or sequence in generated_seqs or balanced not in gen:
            continue
            
        seqs[balanced] += 1
        
        balanced_df.loc[len(balanced_df)] = [sequence, balanced, count]
        generated_seqs.add(sequence)
        
        if seqs[j] >= 1000:
            break
    # print(seqs)

Generating sequences in the following stack depths: [1]


  0%|          | 0/1 [00:00<?, ?it/s]

7
48
20
2
19
28
20
29
36
3
16
14
17
24
41
46
11
18
7
4
19
13
26
20
48
11
46
35
8
29
35
16
21
2
18
27
23
42
9
20
35
3
8
34
30
3
19
46
5
19
39
21
35
8
23
22
36
7
45
18
17
13
42
22
14
5
5
46
6
12
39
6
24
29
43
33
28
44
13
38
10
31
10
35
44
15
7
23
23
39
41
33
11
5
46
7
39
23
18
33
3
22
30
22
37
24
38
48
16
11
10
28
48
18
3
48
32
50
41
15
10
49
39
35
25
2
3
27
9
23
2
13
30
36
34
32
25
13
26
8
40
27
48
30
25
43
38
20
29
23
35
49
38
10
6
43
37
3
41
43
29
15
6
5
22
17
32
20
25
28
30
12
13
12
35
48
10
5
8
6
4
24
13
49
44
46
49
28
21
30
6
7
20
13
13
5
47
10
17
14
31
44
9
45
8
25
18
3
23
23
27
21
27
22
17
35
18
10
30
28
43
3
32
44
34
11
42
21
38
25
4
11
6
45
35
37
31
7
31
36
38
5
9
8
11
3
27
21
14
3
16
7
33
40
36
5
30
19
49
26
27
25
30
24
41
27
45
32
40
34
5
32
9
13
25
44
29
22
42
18
30
3
35
2
19
28
28
18
37
31
43
45
32
11
12
32
15
25
35
13
22
28
20
37
41
26
15
5
35
9
27
16
50
37
22
47
35
11
2
17
46
15
16
35
23
45
38
34
28
20
11
40
3
17
35
3
14
22
34
41
5
38
43
6
19
45
44
2
22
14
6
28
17
40
30
2

KeyboardInterrupt: 

In [115]:

balanced_df = pd.DataFrame(columns=['sequence', 'stack_depth', 'count'])

seqs = [0 for i in range(400)]

generated_seqs = set()

# gen = [i for i in range(2, 10)] + [i for i in range(10, 101, 10)]
gen = [1]
print(f'Generating sequences in the following stack depths: {gen}')

for j in tqdm(gen):
    while True:
        length = 512
        
        depth = random.randint(2, 50)
        print(seqs[j], end='\r')
        sequence = generate_balanced_brackets(length, depth, depth)
        balanced, count = is_balanced(sequence)
        
        if seqs[j] == 2000 or sequence in generated_seqs:
            continue
            
        seqs[j] += 1
        
        balanced_df.loc[len(balanced_df)] = [sequence, balanced, count]
        generated_seqs.add(sequence)
        
        if seqs[j] >= 2000:
            break
    # print(seqs)

Generating sequences in the following stack depths: [1]


  0%|          | 0/1 [00:00<?, ?it/s]

In [116]:
print(len(balanced_df))
balanced_df.head()

2000


sequence  stack_depth  count
0  ()()(()())((())((())()()((()))())())()()((())(...           48      0
1  ()()()()()(()((()((())))((()))())((())))()()((...            6      0
2  ()()()((()())(()()()))(()()())(())(()(()()()()...            3      0
3  (((((((()()(((((()(())(()(()(())())(((()())(()...           44      0
4  (((((())((()((())(()()))()(()(()))(()()()))())...           33      0

In [120]:

unbalanced_data = []
for index, i in tqdm(enumerate(gen), total=len(gen)):
    while len(unbalanced_data) < 1000*(index+1):
        sequence = generate_bracket_sequence(512, i)
        balanced, count = is_balanced(sequence)
        # if balanced != -1*i:
            # print(i, end=' ')
            # continue
        unbalanced_data.append(sequence)
        
    # print(len(unbalanced_data))

print(len(unbalanced_data))
unbalanced_stack_depth = [ is_balanced(sequence) for sequence in unbalanced_data ]

unbalanced_count = [x[1] for x in unbalanced_stack_depth]
unbalanced_stack_depth = [x[0] for x in unbalanced_stack_depth]

  0%|          | 0/1 [00:00<?, ?it/s]

1000


In [168]:
# FOR COUNT DATA
unbalanced_data = []
for index, i in tqdm(enumerate(gen), total=len(gen)):
    while len(unbalanced_data) < 2000*(index+1):
        print(len(unbalanced_data), end='\r')
        sequence = generate_bracket_sequence_2(512, 5)
        balanced, count = is_balanced(sequence)
        # if balanced != -1*i:
            # print(i, end=' ')
            # continue
        unbalanced_data.append(sequence)
        
    # print(len(unbalanced_data))

print(len(unbalanced_data))
unbalanced_stack_depth = [ is_balanced(sequence) for sequence in unbalanced_data ]

unbalanced_count = [x[1] for x in unbalanced_stack_depth]
unbalanced_stack_depth = [x[0] for x in unbalanced_stack_depth]

  0%|          | 0/1 [00:00<?, ?it/s]

2000


In [169]:
unbalanced_data

['(())))()(()(()))(((()()(()(())(())((())()())((()))()(((((()())())(()())))(((((())(())))(()(()(()())))(()()))))((())))(()))(((())()(()(()()())(((())(((())())(((())((()))()()()((((((())()()))()()()()())))))))(((()()())(())))((()(()))())(()()(((((())(()()(((()(((()))(((((())))))(((((((())())(()))))()(()))(())(()())))((())())((())((((()))))))))))))()(((((())()((()(())((())()(())))))())))()()()(())()()))()()))))((()())()((((()())(()(()))(((()()()())(()())))))((()()))((())))(()(()))(()(())((()))((((()(()()()())))',
 '(()())()(()())()))()()(((((((()(()()()))(((()(((())(()(())))(())(()()((())))))()(()()()(()))))))(((())((()(()))())((())()))(()())((()(()())()())))(()(()((())((())()((()((())(((())))((()((((((((((()))())())(())(())())(()()())((()))))(()(())()))()((()))(())(()()(()))))(()((()())()()(()))))(()(((((()((())(()()((()))()()())))()(()))(()(())(()))(()()))(((()())))))))))((())())()())(((()(((((()(())))()))())((()()(()())))()()))))()))()()(())(())())))()(())())((())())()()))(()))()(()((

In [170]:

unbalanced_df = pd.DataFrame({'sequence': unbalanced_data, 'stack_depth': unbalanced_stack_depth, 'count': unbalanced_count}, columns=['sequence', 'stack_depth', 'count'])

In [171]:
unbalanced_df.head()

sequence  stack_depth  count
0  (())))()(()(()))(((()()(()(())(())((())()())((...           -2      4
1  (()())()(()())()))()()(((((((()(()()()))(((()(...           -2      0
2  ((((()(()(((((())(((()()()))(((())(()())())(()...          -18     -2
3  ())))()()))()()()((()((()(()(()))()()())()((()...           -1     -2
4  ((()())(()))(())((())(()(()()))((())())))(((((...           -4      4

In [172]:
bracket_data = pd.concat([balanced_df, unbalanced_df], ignore_index=True)

bracket_data = bracket_data.sample(frac=1).reset_index(drop=True)

In [173]:
bracket_data

sequence  stack_depth  count
0     ()((())))((()()))()(()))())(()(()()(()()()))))...           -3     -4
1     ()((((())(())))())()(((((((()(()))())))())(())...           16      0
2     (((((()(())()()()(()(()((()()()((((()()((())()...          -16      2
3     (())(((())))((()(())())())()()()()()()()()()()...            4      0
4     ((()()))()())))()((()))))()))(()()(()))()()())...           -3     -2
...                                                 ...          ...    ...
3995  (((())))(()(()())(()(((((((()()((()(()((((((()...           30      0
3996  ()(())((())))())()(()(()()(((()()(()((()(()()(...           -3      4
3997  (())(()()()(((((())(((()))()(())))()()))())(((...          -13      2
3998  (())())()())))))((((((()(((())(()())))(((((())...           -2     -2
3999  (()()))))()())))))()))(()())))))))((()))(()()(...           -2      4

[4000 rows x 3 columns]

In [97]:
# find minimum stack depth
min_stack_depth = bracket_data['stack_depth'].min()

min_stack_depth

-122

In [98]:
max_stack_depth = bracket_data['stack_depth'].max()

max_stack_depth

100

In [174]:
bracket_data.to_csv('BRACKET_LOW_COUNT_DATA.csv', index=False)

In [20]:
def generate_no_count(n):
    sequence = ['(' for i in range(n//2)] + [')' for i in range(n//2)]
    sequence = ''.join(sequence)
    # print(sequence, is_balanced(sequence))
    while is_balanced(sequence)[0] > 0:
        # randomly shuffle the sequence
        sequence = ''.join(random.sample(sequence, len(sequence)))
    return sequence

In [48]:
s = generate_no_count(10)
is_balanced(s), s

((-1, 0), '())())()((')

In [104]:
no_count_data = []
for i in tqdm(range(4000)):
    sequence = generate_no_count(512)
    no_count_data.append(sequence)
    
no_count_stack_depth = [ is_balanced(sequence) for sequence in no_count_data ]

no_count_count = [x[1] for x in no_count_stack_depth]
no_count_stack_depth = [x[0] for x in no_count_stack_depth]

no_count_df = pd.DataFrame({'sequence': no_count_data, 'stack_depth': no_count_stack_depth, 'count': no_count_count}, columns=['sequence', 'stack_depth', 'count'])

  0%|          | 0/4000 [00:00<?, ?it/s]

In [105]:
no_count_df.head()

sequence  stack_depth  count
0  ))()((((()((((())())((())()((()()())(())))()((...            0      0
1  ))(()))(()))(())(((()()((()))(())(()(())(()(((...            0      0
2  )(((()(((()())())((()()(((()()()))())(()(())((...            0      0
3  ()))((()())(())))))))(((()(()))())))()(())((()...           -1      0
4  )((()))))()))))((())(()())(())((())()))()))(()...            0      0

In [102]:
no_count_df.to_csv('no_count.csv', index=False)

In [106]:
# append bracket data and no count data
combined_df = pd.concat([bracket_data, no_count_df], ignore_index=True)

combined_df = combined_df.sample(frac=1).reset_index(drop=True)

combined_df.to_csv('balanced_with_no_count.csv', index=False)

In [2]:
import pandas as pd

data = pd.read_csv('balanced_with_no_count.csv')
data2 = pd.read_csv('train-2.csv')

# concat data
data = pd.concat([data, data2], ignore_index=True)

data = data.sample(frac=1).reset_index(drop=True)

data.to_csv('train.csv', index=False)

FileNotFoundError: [Errno 2] No such file or directory: 'train=2.csv'